In [1]:
import pandas as pd
import numpy as np

In [6]:
import numpy as np
import tensorflow as tf
from tensorflow.keras.layers import Embedding, Input, Dense
from tensorflow.keras import layers
from tensorflow.keras.models import Model
from sklearn.model_selection import train_test_split
from tensorflow.keras.optimizers import Adam
from tensorflow.keras.callbacks import EarlyStopping
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.layers import MultiHeadAttention, LayerNormalization, Dense
import keras_nlp
from geopy.distance import geodesic

In [8]:
data = pd.read_csv('city_temperature.csv', low_memory = False)
data = data[(data['Country'] == 'US')]
data = data[['State', 'City', 'Month', 'Day', 'Year', 'AvgTemperature']]
data = data[(data['Month'] == 10) & (data['Year'] >= 2007)]
data = data[~data['State'].isin(['Alaska', 'Hawaii', 'Additional Territories', 'District of Columbia'])].reset_index(drop = True)

### Train: 2007-2012 (6 yrs)
### Validation: 2013-2016 (4 yrs)
### Test: 2017-2019 (3 yrs)

city_per_state = data[['State', 'City']].drop_duplicates().groupby('State', as_index=False).first()
filtered_data = data.merge(city_per_state, on=['State', 'City']).drop_duplicates().reset_index(drop = True)

### Florida -> Jacksonville; Louisiana -> New Orleans
temp = filtered_data[['State', 'City']].drop_duplicates().reset_index(drop = True)
temp['City'] = temp['City'].replace({'Daytona Beach': 'Jacksonville', 'Baton Rouge': 'New Orleans'})
temp = temp[~temp['State'].isin(['Delaware'])].reset_index(drop = True)

temp.to_csv('all_cities.csv', index = False)

### Final data
lat_lon = pd.read_csv('all_cities_lat_lon.csv')
final = data.drop_duplicates().merge(lat_lon, on = ['State', 'City'])
final[final['AvgTemperature'] == -99]

State        City  Month  Day  Year  AvgTemperature   Latitude   
496         Arizona     Phoenix     10    1  2010           -99.0  33.448376  \
497         Arizona     Phoenix     10    2  2010           -99.0  33.448376   
527         Arizona     Phoenix     10    1  2011           -99.0  33.448376   
558         Arizona     Phoenix     10    1  2012           -99.0  33.448376   
651         Arizona     Phoenix     10    1  2015           -99.0  33.448376   
2308    Connecticut  Bridgeport     10   15  2016           -99.0  41.186390   
2309    Connecticut  Bridgeport     10   16  2016           -99.0  41.186390   
2310    Connecticut  Bridgeport     10   17  2016           -99.0  41.186390   
2311    Connecticut  Bridgeport     10   18  2016           -99.0  41.186390   
15101  South Dakota  Rapid City     10    5  2013           -99.0  44.080544   
15102  South Dakota  Rapid City     10    6  2013           -99.0  44.080544   

        Longitude  
496   -112.074036  
497   -112.074036  
527   -112.074036  
558   -112.074036  
651   -112.074036  
2308   -73.195557  
2309   -73.195557  
2310   -73.195557  
2311   -73.195557  
15101 -103.231018  
15102 -103.231018

In [9]:
### Remove Arizona, Connecticut, South Dakota
final = final[~final['State'].isin(['Arizona', 'Connecticut', 'South Dakota'])].reset_index(drop = True)

### State dictionary
all_states = final['State'].unique()
state_dict = {}

for i, state in enumerate(all_states):
    state_dict[state] = i

### Dict of city and coordinates
coord_dict = {}

for state in state_dict:
    idx = state_dict[state]
    coord = lat_lon[lat_lon['State'] == state][['Latitude', 'Longitude']].iloc[0].values
    coord_dict[idx] = list(coord)

In [12]:
### k closest states for each state

def haversine(lat1, lon1, lat2, lon2):
    return geodesic((lat1, lon1), (lat2, lon2)).km

def get_closest_dict(df, k):
    neighbors = []
    
    # Loop over each city in the DataFrame
    for i, row in df.iterrows():
        city = row['City']
        state = row['State']
        lat1, lon1 = row['Latitude'], row['Longitude']
        
        distances = []
        
        # Compare with all other cities
        for j, compare_row in df.iterrows():
            if i != j:  # Don't compare the city to itself
                lat2, lon2 = compare_row['Latitude'], compare_row['Longitude']
                dist = haversine(lat1, lon1, lat2, lon2)
                distances.append((dist, compare_row['State'], compare_row['City']))
        
        distances.sort(key=lambda x: x[0])
        closest_k = distances[:k]
        neighbors.append((state, city, closest_k))
    
    neighbor_df = pd.DataFrame([
        {'State': state, 'City': city, 'Closest Neighbors': neighbors}
        for state, city, neighbors in neighbors
    ])
    
    closest_dict = {}
    for i in range(neighbor_df.shape[0]):
        closest_dict[i] = [state_dict[x[1]] for x in neighbor_df.iloc[i]['Closest Neighbors']]
        
    return closest_dict

In [23]:
### Convert the masked temperature to ZERO

def generate_data(year_min, year_max, closest_dict):
    
    masked_temps = []
    masked_idxs = []
    target_idxs = []
    target_temps = []
    
    for year in range(year_min, year_max + 1):
        for day in range(1, 32):
            
            temp = final[(final['Day'] == day) & (final['Year'] == year)].reset_index(drop = True)
            nrow = temp.shape[0]
            
            for i in range(nrow):
                masked_temp = list(temp.iloc[closest_dict[i]]['AvgTemperature'])
                masked_temps.append(masked_temp)
                
                masked_idx = closest_dict[i]
                masked_idxs.append([coord_dict[t] for t in masked_idx])
                
                target_idxs.append(coord_dict[i])
                
                target_temp = temp.iloc[i]['AvgTemperature']
                target_temps.append(target_temp)                       
                
    return np.array(masked_temps), np.array(masked_idxs), np.array(target_idxs), np.array(target_temps)

In [24]:
def get_test_losses(k_list):
    
    losses = []
    
    for k in k_list:
        
        df = final[['State', 'City', 'Latitude', 'Longitude']].drop_duplicates().reset_index(drop = True)
        closest_dict = get_closest_dict(df, k)
        
        train_masked_temps, train_masked_idxs, train_idxs, train_target_temps \
            = generate_data(2007, 2012, closest_dict)
        
        val_masked_temps, val_masked_idxs, val_idxs, val_target_temps = \
            generate_data(2013, 2016, closest_dict)
        
        test_masked_temps, test_masked_idxs, test_idxs, test_target_temps = \
            generate_data(2017, 2019, closest_dict)
        
        embedding_size = 32
        
        masked_temp_input = layers.Input(shape=(k,), dtype=tf.float32, name="masked_temp_input")
        masked_idx_input = layers.Input(shape=(k,2,), dtype=tf.int32, name="masked_idx_input")
        train_idx_input = layers.Input(shape=(2,), dtype=tf.float32, name="train_idx_input")
        
        dense_relu = layers.Dense(128, activation="relu", 
                                  kernel_initializer=tf.keras.initializers.RandomUniform(minval=-0.01, maxval=0.01),
                                  name="dense_relu")
        dense_linear = layers.Dense(embedding_size, activation="linear", 
                                    kernel_initializer=tf.keras.initializers.RandomUniform(minval=-0.01, maxval=0.01),
                                    name="dense_linear")

        context_embedding = dense_linear(dense_relu(masked_idx_input))
        center_embedding = dense_linear(dense_relu(train_idx_input)) 
        
        masked_temp_input2 = layers.Reshape((k, 1))(masked_temp_input)
        weighted_embeddings = layers.Multiply()([context_embedding, masked_temp_input2])

        sum_embeddings = layers.Lambda(lambda x: tf.reduce_sum(x, axis=1), name="sum_embeddings")(weighted_embeddings)

        center_embedding_flat = layers.Flatten()(center_embedding)
        lambda_output = layers.Dot(axes=-1, name="dot_product")([sum_embeddings, center_embedding_flat])

        model = Model(inputs=[masked_temp_input, masked_idx_input, train_idx_input], outputs=lambda_output)
        
        model.compile(optimizer=Adam(learning_rate = 1e-3), loss='mean_squared_error')

        # Fit the model with validation data
        history = model.fit(
            [train_masked_temps, train_masked_idxs, train_idxs], 
            train_target_temps,        
            validation_data=([val_masked_temps, val_masked_idxs, val_idxs], val_target_temps),  
            epochs=2000,                 
            batch_size=10000
        )
        
        test_loss = model.evaluate([test_masked_temps, test_masked_idxs, test_idxs], test_target_temps)
        losses.append(test_loss)
    
    return losses

In [25]:
exp_results = get_test_losses([5, 10, 15, 20, 25, 30, 35, 40])

Epoch 1/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 1s/step - loss: 2480.7507 - val_loss: 283.9029
Epoch 2/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 262ms/step - loss: 273.6025 - val_loss: 10016.3086
Epoch 3/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 229ms/step - loss: 9227.0908 - val_loss: 713.3654
Epoch 4/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 294ms/step - loss: 653.1506 - val_loss: 697.0093
Epoch 5/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 226ms/step - loss: 669.0896 - val_loss: 1787.8929
Epoch 6/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 224ms/step - loss: 1694.5498 - val_loss: 2457.2903
Epoch 7/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 221ms/step - loss: 2321.2537 - val_loss: 2774.8716
Epoch 8/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 225ms/step - loss: 2618.2747 - val_loss: 2893.3340
Epoch 9/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 226ms/step - loss: 2729.0432 - val_loss: 2897.5576
Epoch 10/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 223ms/step - loss: 2733.0098 - val_loss: 2824.8181
Epoch 11/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 221ms/step - loss: 2665.0193 - val_loss: 2686

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 220ms/step - loss: 183.3044 - val_loss: 188.0014
Epoch 67/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 225ms/step - loss: 178.0359 - val_loss: 181.9885
Epoch 68/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 250ms/step - loss: 173.1670 - val_loss: 179.1087
Epoch 69/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 222ms/step - loss: 171.2511 - val_loss: 179.2417
Epoch 70/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 221ms/step - loss: 172.0034 - val_loss: 180.1475
Epoch 71/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 229ms/step - loss: 173.2244 - val_loss: 179.7150
Epoch 72/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 224ms/step - loss: 172.9011 - val_loss: 177.4485
Epoch 73/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 224ms/step - loss: 170.5840 - val_loss: 174.4889
Epoch 74/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 222ms/step - loss: 167.3985 - val_loss: 172.5056
Epoch 75/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 222ms/step - loss: 165.0022 - val_loss: 172.2786
Epoch 76/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 217ms/step - loss: 164.2462 - val_loss: 173.0676
Epoch 77/2000

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 250ms/step - loss: 128.1775 - val_loss: 133.1273
Epoch 132/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 224ms/step - loss: 127.7891 - val_loss: 132.7310
Epoch 133/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 234ms/step - loss: 127.4035 - val_loss: 132.3507
Epoch 134/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 216ms/step - loss: 127.0271 - val_loss: 131.9817
Epoch 135/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 218ms/step - loss: 126.6625 - val_loss: 131.6139
Epoch 136/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 220ms/step - loss: 126.3065 - val_loss: 131.2384
Epoch 137/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 223ms/step - loss: 125.9545 - val_loss: 130.8543
Epoch 138/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 222ms/step - loss: 125.6051 - val_loss: 130.4691
Epoch 139/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 225ms/step - loss: 125.2615 - val_loss: 130.0921
Epoch 140/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 228ms/step - loss: 124.9270 - val_loss: 129.7283
Epoch 141/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 218ms/step - loss: 124.6012 - val_loss: 129.3782
Epo

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 225ms/step - loss: 112.1199 - val_loss: 116.1079
Epoch 197/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 223ms/step - loss: 111.9429 - val_loss: 115.9156
Epoch 198/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 233ms/step - loss: 111.7666 - val_loss: 115.7240
Epoch 199/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 236ms/step - loss: 111.5908 - val_loss: 115.5341
Epoch 200/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 223ms/step - loss: 111.4155 - val_loss: 115.3466
Epoch 201/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 235ms/step - loss: 111.2406 - val_loss: 115.1607
Epoch 202/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 221ms/step - loss: 111.0662 - val_loss: 114.9752
Epoch 203/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 221ms/step - loss: 110.8922 - val_loss: 114.7894
Epoch 204/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 305ms/step - loss: 110.7187 - val_loss: 114.6027
Epoch 205/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 218ms/step - loss: 110.5454 - val_loss: 114.4155
Epoch 206/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 223ms/step - loss: 110.3723 - val_loss: 114.2282
Epo

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 233ms/step - loss: 101.0097 - val_loss: 104.1991
Epoch 262/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 223ms/step - loss: 100.8398 - val_loss: 104.0173
Epoch 263/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 296ms/step - loss: 100.6700 - val_loss: 103.8351
Epoch 264/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 220ms/step - loss: 100.5000 - val_loss: 103.6528
Epoch 265/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 221ms/step - loss: 100.3301 - val_loss: 103.4709
Epoch 266/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 230ms/step - loss: 100.1604 - val_loss: 103.2897
Epoch 267/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 221ms/step - loss: 99.9905 - val_loss: 103.1089
Epoch 268/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 222ms/step - loss: 99.8205 - val_loss: 102.9285
Epoch 269/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 235ms/step - loss: 99.6507 - val_loss: 102.7476
Epoch 270/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 229ms/step - loss: 99.4809 - val_loss: 102.5659
Epoch 271/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 222ms/step - loss: 99.3111 - val_loss: 102.3836
Epoch 27

...

1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 521ms/step - loss: 60.1506 - val_loss: 53.2596
Epoch 1682/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 524ms/step - loss: 60.8918 - val_loss: 55.5866
Epoch 1683/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 512ms/step - loss: 62.8393 - val_loss: 56.0843
Epoch 1684/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 507ms/step - loss: 63.6537 - val_loss: 61.0005
Epoch 1685/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 492ms/step - loss: 67.8979 - val_loss: 57.3828
Epoch 1686/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 512ms/step - loss: 64.9314 - val_loss: 58.6877
Epoch 1687/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 521ms/step - loss: 65.8024 - val_loss: 53.7418
Epoch 1688/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 511ms/step - loss: 61.4373 - val_loss: 51.9820
Epoch 1689/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 528ms/step - loss: 59.6326 - val_loss: 53.7350
Epoch 1690/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 518ms/step - loss: 61.0746 - val_loss: 57.2594
Epoch 1691/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 516ms/step - loss: 64.6237 - val_loss: 66.5497
Epoch 1692/2000

1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 516ms/step - loss: 58.1023 - val_loss: 51.6733
Epoch 1747/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 519ms/step - loss: 59.0629 - val_loss: 52.0041
Epoch 1748/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 525ms/step - loss: 59.5732 - val_loss: 54.7863
Epoch 1749/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 508ms/step - loss: 61.9024 - val_loss: 53.6508
Epoch 1750/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 511ms/step - loss: 61.1600 - val_loss: 55.0103
Epoch 1751/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 500ms/step - loss: 62.1359 - val_loss: 52.1996
Epoch 1752/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 507ms/step - loss: 59.8172 - val_loss: 52.4831
Epoch 1753/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 477ms/step - loss: 59.8571 - val_loss: 51.0012
Epoch 1754/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 504ms/step - loss: 58.7016 - val_loss: 50.3623
Epoch 1755/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 527ms/step - loss: 57.9147 - val_loss: 49.6502
Epoch 1756/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 528ms/step - loss: 57.2878 - val_loss: 49.7171
Epoch 1757/2000

1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 512ms/step - loss: 55.7860 - val_loss: 48.7325
Epoch 1812/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 542ms/step - loss: 56.2466 - val_loss: 49.8754
Epoch 1813/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 518ms/step - loss: 57.4302 - val_loss: 52.8909
Epoch 1814/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 516ms/step - loss: 60.0555 - val_loss: 53.4215
Epoch 1815/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 515ms/step - loss: 60.8732 - val_loss: 58.1152
Epoch 1816/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 544ms/step - loss: 64.9210 - val_loss: 53.8591
Epoch 1817/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 508ms/step - loss: 61.3311 - val_loss: 55.3423
Epoch 1818/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 508ms/step - loss: 62.3603 - val_loss: 50.8383
Epoch 1819/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 510ms/step - loss: 58.4766 - val_loss: 49.3651
Epoch 1820/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 497ms/step - loss: 56.8559 - val_loss: 48.0567
Epoch 1821/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 531ms/step - loss: 55.7219 - val_loss: 48.1392
Epoch 1822/2000

1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 534ms/step - loss: 56.6968 - val_loss: 47.2184
Epoch 1877/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 516ms/step - loss: 54.9472 - val_loss: 46.6146
Epoch 1878/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 532ms/step - loss: 54.4149 - val_loss: 47.5310
Epoch 1879/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 508ms/step - loss: 55.3167 - val_loss: 51.1927
Epoch 1880/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 511ms/step - loss: 58.4416 - val_loss: 52.3290
Epoch 1881/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 509ms/step - loss: 59.7491 - val_loss: 59.7198
Epoch 1882/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 474ms/step - loss: 66.2688 - val_loss: 53.3740
Epoch 1883/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 503ms/step - loss: 60.6471 - val_loss: 52.5666
Epoch 1884/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 523ms/step - loss: 59.6004 - val_loss: 47.7653
Epoch 1885/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 515ms/step - loss: 55.3320 - val_loss: 46.7272
Epoch 1886/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 528ms/step - loss: 54.3294 - val_loss: 47.9523
Epoch 1887/2000

1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 532ms/step - loss: 56.7016 - val_loss: 48.8473
Epoch 1942/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 526ms/step - loss: 56.1817 - val_loss: 46.1908
Epoch 1943/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 507ms/step - loss: 53.9045 - val_loss: 45.4101
Epoch 1944/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 499ms/step - loss: 53.1046 - val_loss: 45.6204
Epoch 1945/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 465ms/step - loss: 53.2624 - val_loss: 46.2852
Epoch 1946/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 544ms/step - loss: 53.9870 - val_loss: 48.2082
Epoch 1947/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 486ms/step - loss: 55.5882 - val_loss: 48.1579
Epoch 1948/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 495ms/step - loss: 55.7545 - val_loss: 50.1622
Epoch 1949/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 520ms/step - loss: 57.3778 - val_loss: 48.3095
Epoch 1950/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 568ms/step - loss: 55.8865 - val_loss: 48.4857
Epoch 1951/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 513ms/step - loss: 55.8184 - val_loss: 46.5369
Epoch 1952/2000

In [26]:
exp_results

[22.684772491455078,
 29.91735076904297,
 34.258609771728516,
 40.50286865234375,
 47.626365661621094,
 52.71220016479492,
 60.98051834106445,
 75.5508804321289]

In [27]:
exp_results_2 = get_test_losses([1, 2, 3, 4])

Epoch 1/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 1s/step - loss: 3040.7502 - val_loss: 2349.6865
Epoch 2/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 103ms/step - loss: 2218.7593 - val_loss: 925.3418
Epoch 3/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 99ms/step - loss: 880.7038 - val_loss: 516.1438
Epoch 4/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 92ms/step - loss: 476.1152 - val_loss: 1054.6862
Epoch 5/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 101ms/step - loss: 970.9456 - val_loss: 344.2723
Epoch 6/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 118ms/step - loss: 319.9135 - val_loss: 344.1308
Epoch 7/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 98ms/step - loss: 329.6483 - val_loss: 581.9951
Epoch 8/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 97ms/step - loss: 556.2373 - val_loss: 666.9700
Epoch 9/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 103ms/step - loss: 636.5807 - val_loss: 568.1653
Epoch 10/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 100ms/step - loss: 542.9906 - val_loss: 376.1368
Epoch 11/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 102ms/step - loss: 360.3080 - val_loss: 255.3218
Epoch 12/20

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 98ms/step - loss: 147.8697 - val_loss: 154.0344
Epoch 67/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 101ms/step - loss: 146.4297 - val_loss: 154.1077
Epoch 68/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 99ms/step - loss: 146.3764 - val_loss: 153.8126
Epoch 69/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 102ms/step - loss: 146.0931 - val_loss: 152.2747
Epoch 70/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 106ms/step - loss: 144.7655 - val_loss: 151.3275
Epoch 71/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 104ms/step - loss: 144.0327 - val_loss: 151.2443
Epoch 72/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 102ms/step - loss: 144.0590 - val_loss: 150.6081
Epoch 73/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 109ms/step - loss: 143.4742 - val_loss: 149.6158
Epoch 74/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 101ms/step - loss: 142.4848 - val_loss: 149.3919
Epoch 75/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 102ms/step - loss: 142.2088 - val_loss: 149.2853
Epoch 76/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 116ms/step - loss: 142.1004 - val_loss: 148.4471
Epoch 77/2000
1

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 101ms/step - loss: 126.3476 - val_loss: 131.7052
Epoch 132/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 103ms/step - loss: 126.0626 - val_loss: 131.4020
Epoch 133/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 102ms/step - loss: 125.7790 - val_loss: 131.1012
Epoch 134/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 102ms/step - loss: 125.4987 - val_loss: 130.7983
Epoch 135/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 93ms/step - loss: 125.2174 - val_loss: 130.4921
Epoch 136/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 103ms/step - loss: 124.9329 - val_loss: 130.1828
Epoch 137/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 101ms/step - loss: 124.6450 - val_loss: 129.8733
Epoch 138/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 112ms/step - loss: 124.3566 - val_loss: 129.5665
Epoch 139/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 100ms/step - loss: 124.0710 - val_loss: 129.2585
Epoch 140/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 101ms/step - loss: 123.7856 - val_loss: 128.9487
Epoch 141/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 114ms/step - loss: 123.4986 - val_loss: 128.6375
Epoc

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 99ms/step - loss: 106.7784 - val_loss: 110.5949
Epoch 197/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 99ms/step - loss: 106.4571 - val_loss: 110.2495
Epoch 198/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 102ms/step - loss: 106.1336 - val_loss: 109.9066
Epoch 199/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 105ms/step - loss: 105.8134 - val_loss: 109.5534
Epoch 200/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 102ms/step - loss: 105.4860 - val_loss: 109.2001
Epoch 201/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 103ms/step - loss: 105.1601 - val_loss: 108.8488
Epoch 202/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 99ms/step - loss: 104.8335 - val_loss: 108.5012
Epoch 203/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 109ms/step - loss: 104.5074 - val_loss: 108.1518
Epoch 204/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 93ms/step - loss: 104.1819 - val_loss: 107.7986
Epoch 205/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 106ms/step - loss: 103.8528 - val_loss: 107.4444
Epoch 206/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 95ms/step - loss: 103.5267 - val_loss: 107.0909
Epoch 20

Epoch 262/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 96ms/step - loss: 83.6238 - val_loss: 85.6579
Epoch 263/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 100ms/step - loss: 83.2422 - val_loss: 85.1784
Epoch 264/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 96ms/step - loss: 82.8012 - val_loss: 84.8146
Epoch 265/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 98ms/step - loss: 82.4730 - val_loss: 84.3638
Epoch 266/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 99ms/step - loss: 82.0312 - val_loss: 83.9490
Epoch 267/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 104ms/step - loss: 81.6438 - val_loss: 83.5497
Epoch 268/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 102ms/step - loss: 81.2901 - val_loss: 83.0667
Epoch 269/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 100ms/step - loss: 80.8308 - val_loss: 82.6844
Epoch 270/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 100ms/step - loss: 80.4745 - val_loss: 82.2493
Epoch 271/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 95ms/step - loss: 80.0845 - val_loss: 81.8111
Epoch 272/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 104ms/step - loss: 79.6725 - val_loss: 81.4119
Epoch 273/2000


...

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 105ms/step - loss: 21.1494 - val_loss: 19.8469
Epoch 1724/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 117ms/step - loss: 21.1807 - val_loss: 19.7281
Epoch 1725/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 118ms/step - loss: 21.2336 - val_loss: 20.0298
Epoch 1726/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 115ms/step - loss: 21.3084 - val_loss: 19.8885
Epoch 1727/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 114ms/step - loss: 21.4337 - val_loss: 20.4075
Epoch 1728/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 117ms/step - loss: 21.5984 - val_loss: 20.2987
Epoch 1729/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 132ms/step - loss: 21.8926 - val_loss: 21.2064
Epoch 1730/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 110ms/step - loss: 22.2519 - val_loss: 21.2787
Epoch 1731/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 109ms/step - loss: 22.9225 - val_loss: 22.7301
Epoch 1732/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 113ms/step - loss: 23.5528 - val_loss: 23.2494
Epoch 1733/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 110ms/step - loss: 24.9235 - val_loss: 25.0268
Epoch 1734/2000

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 110ms/step - loss: 21.1251 - val_loss: 19.7794
Epoch 1789/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 110ms/step - loss: 21.1361 - val_loss: 19.6700
Epoch 1790/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 116ms/step - loss: 21.1430 - val_loss: 19.7911
Epoch 1791/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 109ms/step - loss: 21.1431 - val_loss: 19.6671
Epoch 1792/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 111ms/step - loss: 21.1385 - val_loss: 19.7673
Epoch 1793/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 115ms/step - loss: 21.1284 - val_loss: 19.6585
Epoch 1794/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 106ms/step - loss: 21.1172 - val_loss: 19.7313
Epoch 1795/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 119ms/step - loss: 21.1078 - val_loss: 19.6579
Epoch 1796/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 120ms/step - loss: 21.0996 - val_loss: 19.6994
Epoch 1797/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 111ms/step - loss: 21.0922 - val_loss: 19.6635
Epoch 1798/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 116ms/step - loss: 21.0883 - val_loss: 19.6766
Epoch 1799/2000

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 119ms/step - loss: 21.3542 - val_loss: 19.9393
Epoch 1854/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 107ms/step - loss: 21.2396 - val_loss: 19.6695
Epoch 1855/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 127ms/step - loss: 21.1555 - val_loss: 19.7253
Epoch 1856/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 122ms/step - loss: 21.0999 - val_loss: 19.6523
Epoch 1857/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 125ms/step - loss: 21.0765 - val_loss: 19.6469
Epoch 1858/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 113ms/step - loss: 21.0800 - val_loss: 19.7408
Epoch 1859/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 110ms/step - loss: 21.1041 - val_loss: 19.6660
Epoch 1860/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 107ms/step - loss: 21.1395 - val_loss: 19.8545
Epoch 1861/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 116ms/step - loss: 21.1731 - val_loss: 19.7115
Epoch 1862/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 107ms/step - loss: 21.2085 - val_loss: 19.9500
Epoch 1863/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 113ms/step - loss: 21.2386 - val_loss: 19.7628
Epoch 1864/2000

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 120ms/step - loss: 21.2296 - val_loss: 19.6797
Epoch 1919/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 115ms/step - loss: 21.1579 - val_loss: 19.7570
Epoch 1920/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 111ms/step - loss: 21.1039 - val_loss: 19.6395
Epoch 1921/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 121ms/step - loss: 21.0718 - val_loss: 19.6567
Epoch 1922/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 112ms/step - loss: 21.0593 - val_loss: 19.6731
Epoch 1923/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 109ms/step - loss: 21.0631 - val_loss: 19.6332
Epoch 1924/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 116ms/step - loss: 21.0789 - val_loss: 19.7549
Epoch 1925/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 114ms/step - loss: 21.1045 - val_loss: 19.6628
Epoch 1926/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 111ms/step - loss: 21.1444 - val_loss: 19.9013
Epoch 1927/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 126ms/step - loss: 21.2003 - val_loss: 19.7647
Epoch 1928/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 120ms/step - loss: 21.2832 - val_loss: 20.1554
Epoch 1929/2000

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 115ms/step - loss: 21.0606 - val_loss: 19.6790
Epoch 1984/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 115ms/step - loss: 21.0554 - val_loss: 19.6347
Epoch 1985/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 108ms/step - loss: 21.0521 - val_loss: 19.6643
Epoch 1986/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 116ms/step - loss: 21.0497 - val_loss: 19.6376
Epoch 1987/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 116ms/step - loss: 21.0482 - val_loss: 19.6558
Epoch 1988/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 115ms/step - loss: 21.0470 - val_loss: 19.6402
Epoch 1989/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 120ms/step - loss: 21.0458 - val_loss: 19.6481
Epoch 1990/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 109ms/step - loss: 21.0450 - val_loss: 19.6405
Epoch 1991/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 108ms/step - loss: 21.0444 - val_loss: 19.6439
Epoch 1992/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 123ms/step - loss: 21.0438 - val_loss: 19.6407
Epoch 1993/2000
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 110ms/step - loss: 21.0431 - val_loss: 19.6425
Epoch 1994/2000

In [29]:
exp_results_2

[37.39491271972656, 31.90117645263672, 23.062381744384766, 22.766298294067383]